In [6]:
import os
import pandas as pd
import numpy as np
import matplotlib
from pyspark.sql import SparkSession
from pyspark.sql import functions
from pyspark.sql.types import StructType
from pyspark import SparkContext, SparkConf, SQLContext
from pyspark.sql.types import FloatType
from pyspark.sql.functions import udf


In [13]:
aeroptos = pd.read_csv('/Users/marioriveravargas/Desktop/MIAD/MODELADO DE DATOS Y ETL/ARCHIVOS DEL GITHUB CON RECURSOS  DE TALLERES Y LABS/Recursos-main/Infraestructura visible/Etapa 1/aeropuertos.csv')
print(aeroptos)
vuelos = pd.read_csv('/Users/marioriveravargas/Desktop/MIAD/MODELADO DE DATOS Y ETL/ARCHIVOS DEL GITHUB CON RECURSOS  DE TALLERES Y LABS/Recursos-main/Infraestructura visible/Etapa 1/vuelos.csv')
print(vuelos)
aeroptos=aeroptos.drop('Unnamed: 0', axis=1)

     Unnamed: 0 sigla iata                 nombre           municipio  \
0           274   BOG  BOG              EL DORADO        Bogotá, D.C.   
1           134   9DG  NaN           EL LAGO - CA             Piedras   
2           803   TLU  TLU                   TOLU          Tolú Viejo   
3           174   9MK  NaN         VILLA ISABELLA            Trinidad   
4           344   CUC  CUC            CAMILO DAZA  San José de Cúcuta   
..          ...   ...  ...                    ...                 ...   
287         855   VVU  NaN           SANTA ISABEL       Villavicencio   
288         857   YAP  NaN                 YAPIMA                Mitú   
289         858   YOP  NaN             TROMPILLOS               Yopal   
290         860   YPP  NaN         GERMAN ALBERTO               Yopal   
291         862   ZPS  AZT  GUILLERMO GOMEZ ORTIZ            Zapatoca   

           departamento      categoria  latitud  longitud  \
0          Bogotá, D.C.  Internacional   4.7017  -74.1469   
1

In [14]:

import pandas_profiling as pp
pf_vuelos = pp.ProfileReport(vuelos)
pf_aeroptos = pp.ProfileReport(aeroptos)

pf_vuelos 

#print(vuelos.dtypes)
#print(aeroptos.dtypes)
#print(vuelos.describe())
#print(aeroptos.describe())

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [15]:
pf_aeroptos

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [16]:
vuelos.dtypes


ano                 int64
mes                 int64
origen             object
destino            object
tipo_equipo        object
tipo_vuelo         object
trafico            object
empresa            object
vuelos            float64
sillas            float64
carga_ofrecida    float64
pasajeros         float64
carga_bordo       float64
dtype: object

In [17]:
aeroptos.dtypes

sigla                    object
iata                     object
nombre                   object
municipio                object
departamento             object
categoria                object
latitud                 float64
longitud                float64
propietario              object
explotador               object
longitud_pista          float64
ancho_pista             float64
pbmo                    float64
elevacion               float64
resolucion               object
fecha_construccion       object
fecha_vigencia           object
clase                    object
tipo                     object
numero_vuelos_origen    float64
gcd_departamento          int64
gcd_municipio             int64
dtype: object

In [18]:
vuelos.describe()

ano           mes        vuelos        sillas  carga_ofrecida  \
count  67599.000000  67599.000000  66017.000000  63582.000000    6.759900e+04   
mean    2011.592864      6.674359     14.263735   1133.122535    4.675849e+04   
std        1.116215      3.442955     40.198515   4468.301902    2.306673e+05   
min     2010.000000      1.000000      1.000000      0.000000    0.000000e+00   
25%     2011.000000      4.000000      1.000000      0.000000    0.000000e+00   
50%     2012.000000      7.000000      2.000000      0.000000    0.000000e+00   
75%     2013.000000     10.000000      9.000000    240.000000    9.000000e+03   
max     2013.000000     12.000000   2004.000000  79925.000000    7.361385e+06   

          pasajeros   carga_bordo  
count  64116.000000  6.759900e+04  
mean     911.728430  5.325678e+03  
std     3613.766211  2.341590e+04  
min        0.000000  0.000000e+00  
25%        2.000000  0.000000e+00  
50%        8.000000  1.100000e+02  
75%      184.000000  1.338000e+03  
max    65195.000000  1.062015e+06

In [19]:
aeroptos.describe()

latitud    longitud  longitud_pista  ancho_pista          pbmo  \
count  292.000000  292.000000      292.000000   292.000000    237.000000   
mean     5.543336  -73.246114      962.445205    17.633562   5683.341772   
std      2.382669    2.296074      540.019110    10.356164   9669.194412   
min     -0.783100  -81.711300      200.000000    10.000000    400.000000   
25%      4.223250  -74.922400      700.000000    10.000000   2000.000000   
50%      5.307250  -73.045150      800.000000    15.000000   2000.000000   
75%      6.822350  -71.609450     1200.000000    20.000000   4500.000000   
max     13.357200  -67.077600     3800.000000    75.000000  63196.000000   

         elevacion  numero_vuelos_origen  gcd_departamento  gcd_municipio  
count   292.000000          2.210000e+02        292.000000     292.000000  
mean   1073.308219          1.855764e+05         63.037671   63341.636986  
std    1580.858623          3.121902e+05         27.461350   27463.258043  
min       0.000000          1.000000e+00          5.000000    5031.000000  
25%     357.000000          5.100000e+01         50.000000   50001.000000  
50%     597.000000          5.850000e+03         73.000000   73275.000000  
75%     870.000000          2.403310e+05         85.000000   85250.000000  
max    9740.000000          1.804153e+06         99.000000   99773.000000